# Deep Q-Learning 

For this assignment we will implement the Deep Q-Learning algorithm with Experience Replay as described in breakthrough paper __"Playing Atari with Deep Reinforcement Learning"__. We will train an agent to play the famous game of __Breakout__.

In [1]:
import sys
import gym
import torch
import pylab
import random
import numpy as np
import time
from collections import deque
from datetime import datetime
from copy import deepcopy
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.autograd import Variable
from utils import *
from agent import *
from model import *
from config import *
from env import GameEnv
%matplotlib inline
%load_ext autoreload
%autoreload 2

## Understanding the environment

In the following cell, we initialise our game of __Breakout__ and you can see how the environment looks like. For further documentation of the of the environment refer to https://gym.openai.com/envs. 

In [2]:
envs = []
for i in range(num_envs):
    envs.append(GameEnv('SpaceInvadersDeterministic-v4'))
#env.render()

/usr/local/lib/python3.5/dist-packages/skimage/transform/_warps.py:110: UserWarning: Anti-aliasing will be enabled by default in skimage 0.15 to avoid aliasing artifacts when down-sampling images.
  warn("Anti-aliasing will be enabled by default in skimage 0.15 to "


In [3]:
number_lives = envs[0].life
state_size = envs[0].observation_space.shape
action_size = envs[0].action_space.n
rewards, episodes = [], []

## Creating a DQN Agent

Here we create a DQN Agent. This agent is defined in the __agent.py__. The corresponding neural network is defined in the __model.py__. 

__Evaluation Reward__ : The average reward received in the past 100 episodes/games.

__Frame__ : Number of frames processed in total.

__Memory Size__ : The current size of the replay memory.

In [4]:
agent = Agent(action_size)
torch.save(agent.policy_net.state_dict(), "./save_model/spaceinvaders_ppo_best")
evaluation_reward = deque(maxlen=evaluation_reward_length)
frame = 0
memory_size = 0
reset_max = 10

### Main Training Loop

In [2]:
vis_env_idx = 0
vis_env = envs[vis_env_idx]
e = 0
frame = 0
max_eval = -np.inf
reset_count = 0

while (frame < 10000000):
    step = 0
    assert(num_envs * env_mem_size == train_frame)
    frame_next_vals = []
    for i in range(num_envs):
        env = envs[i]
        #history = env.history
        #life = env.life
        #state, reward, done, info = [env.state, env.reward, env.done, env.info]
        for j in range(env_mem_size):
            step += 1
            frame += 1
            
            curr_state = env.history[HISTORY_SIZE-1,:,:]
            action, value = agent.get_action(np.float32(env.history[:HISTORY_SIZE,:,:]) / 255.)
            
            next_state, env.reward, env.done, env.info = env.step(action)
            
            if (i == vis_env_idx):
                vis_env._env.render()
            
            frame_next_state = get_frame(next_state)
            env.history[HISTORY_SIZE,:,:] = frame_next_state
            terminal_state = check_live(env.life, env.info['ale.lives'])
            
            env.life = env.info['ale.lives']
            r = env.reward
            
            agent.memory.push(i, deepcopy(curr_state), action, r, terminal_state, value, 0, 0)
            if (j == env_mem_size-1):
                _, frame_next_val = agent.get_action(np.float32(env.history[1:,:,:]) / 255.)
                frame_next_vals.append(frame_next_val)
            env.score += r
            env.history[:HISTORY_SIZE, :, :] = env.history[1:,:,:]
            
            if (env.done):
                if (e % 50 == 0):
                    print('now time : ', datetime.now())
                    rewards.append(np.mean(evaluation_reward))
                    episodes.append(e)
                    pylab.plot(episodes, rewards, 'b')
                    pylab.savefig("./save_graph/spaceinvaders_ppo.png")
                    torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")
                    
                    if np.mean(evaluation_reward) > max_eval:
                        torch.save(agent.policy_net.state_dict(), "./save_model/spaceinvaders_ppo_best")
                        max_eval = float(np.mean(evaluation_reward))
                        reset_count = 0
                    elif e > 5000:
                        reset_count += 1
                        """
                        if (reset_count == reset_max):
                            print("Training went nowhere, starting again at best model")
                            agent.policy_net.load_state_dict(torch.load("./save_model/spaceinvaders_ppo_best"))
                            agent.update_target_net()
                            reset_count = 0
                        """
                e += 1
                evaluation_reward.append(env.score)
                print("episode:", e, "  score:", env.score,  " epsilon:", agent.epsilon, "   steps:", step,
                  " evaluation reward:", np.mean(evaluation_reward))
                
                env.done = False
                env.score = 0
                env.history = np.zeros([HISTORY_SIZE+1,84,84], dtype=np.uint8)
                env.state = env.reset()
                env.life = number_lives
                get_init_state(env.history, env.state)
                
                
                
    agent.train_policy_net(frame, frame_next_vals)
    agent.update_target_net()


SyntaxError: EOF while scanning triple-quoted string literal (<ipython-input-2-34ccbcc99089>, line 82)

In [ ]:
torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")

In [ ]:
### Loop through all environments and run PPO on them

env_names = ['Asterix-v0', 'Asteroids-v0', 'Atlantis-v0', 'Alien-v0', 'Amidar-v0', 'Assault-v0', 'BankHeist-v0', 'MsPacman-v0']

for a in range(len(env_names)):
    name = env_names[a]
    print("\n\n\n ------- STARTING TRAINING FOR %s ------- \n\n\n" % (name))
    
    envs = []
    for i in range(num_envs):
        envs.append(GameEnv(name))
    #env.render()

    number_lives = envs[0].life
    state_size = envs[0].observation_space.shape
    action_size = envs[0].action_space.n
    rewards, episodes = [], []

    vis_env_idx = 0
    vis_env = envs[vis_env_idx]
    e = 0
    frame = 0
    max_eval = -np.inf
    reset_count = 0


    agent = Agent(action_size)
    torch.save(agent.policy_net.state_dict(), "./save_model/" + name + "_best")
    evaluation_reward = deque(maxlen=evaluation_reward_length)
    frame = 0
    memory_size = 0
    reset_max = 10
    
    print("Determing min/max rewards of environment")
    [low, high] = score_range = get_score_range(name)
    print("Min: %d. Max: %d." % (low, high))

    while (frame < 10000000):
        step = 0
        assert(num_envs * env_mem_size == train_frame)
        frame_next_vals = []
        for i in range(num_envs):
            env = envs[i]
            #history = env.history
            #life = env.life
            #state, reward, done, info = [env.state, env.reward, env.done, env.info]
            for j in range(env_mem_size):
                step += 1
                frame += 1

                curr_state = env.history[HISTORY_SIZE-1,:,:]
                action, value = agent.get_action(np.float32(env.history[:HISTORY_SIZE,:,:]) / 255.)

                next_state, env.reward, env.done, env.info = env.step(action)

                if (i == vis_env_idx):
                    vis_env._env.render()

                frame_next_state = get_frame(next_state)
                env.history[HISTORY_SIZE,:,:] = frame_next_state
                terminal_state = check_live(env.life, env.info['ale.lives'])

                env.life = env.info['ale.lives']
                r = ((env.reward - low) / (high - low)) * 10

                agent.memory.push(i, deepcopy(curr_state), action, r, terminal_state, value, 0, 0)
                if (j == env_mem_size-1):
                    _, frame_next_val = agent.get_action(np.float32(env.history[1:,:,:]) / 255.)
                    frame_next_vals.append(frame_next_val)
                env.score += env.reward
                env.history[:HISTORY_SIZE, :, :] = env.history[1:,:,:]

                if (env.done):
                    if (e % 50 == 0):
                        print('now time : ', datetime.now())
                        rewards.append(np.mean(evaluation_reward))
                        episodes.append(e)
                        pylab.plot(episodes, rewards, 'b')
                        pylab.savefig("./save_graph/" + name + "_ppo.png")
                        torch.save(agent.policy_net, "./save_model/" + name + "_ppo")

                        if np.mean(evaluation_reward) > max_eval:
                            torch.save(agent.policy_net.state_dict(), "./save_model/"  + name + "_ppo_best")
                            max_eval = float(np.mean(evaluation_reward))
                            reset_count = 0
                        elif e > 5000:
                            reset_count += 1
                            """
                            if (reset_count == reset_max):
                                print("Training went nowhere, starting again at best model")
                                agent.policy_net.load_state_dict(torch.load("./save_model/spaceinvaders_ppo_best"))
                                agent.update_target_net()
                                reset_count = 0
                            """
                    e += 1
                    evaluation_reward.append(env.score)
                    print("episode:", e, "  score:", env.score,  " epsilon:", agent.epsilon, "   steps:", step,
                      " evaluation reward:", np.mean(evaluation_reward))

                    env.done = False
                    env.score = 0
                    env.history = np.zeros([HISTORY_SIZE+1,84,84], dtype=np.uint8)
                    env.state = env.reset()
                    env.life = number_lives
                    get_init_state(env.history, env.state)



        agent.train_policy_net(frame, frame_next_vals)
        agent.update_target_net()
    print("FINISHED TRAINING FOR %s" % (name))
    pylab.figure()

/usr/local/lib/python3.5/dist-packages/skimage/transform/_warps.py:110: UserWarning: Anti-aliasing will be enabled by default in skimage 0.15 to avoid aliasing artifacts when down-sampling images.
  warn("Anti-aliasing will be enabled by default in skimage 0.15 to "
/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/model.py:45: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  probs = F.softmax(x[:,:self.action_size] - torch.max(x[:,:self.action_size],1)[0].unsqueeze(1))


Training network. lr: 0.000250. clip: 0.100000


/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/agent.py:255: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number
  pol_loss += pol_avg.detach().cpu()[0]
/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/agent.py:256: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number
  vf_loss += value_loss.detach().cpu()[0]
/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/agent.py:257: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number
  ent_total += ent.detach().cpu()[0]


Iteration 1: Policy loss: -0.134242. Value loss: 0.025672. Entropy: 1.384760.
Iteration 2: Policy loss: -0.134622. Value loss: 0.024417. Entropy: 1.382654.
Iteration 3: Policy loss: -0.138663. Value loss: 0.025462. Entropy: 1.380519.
Training network. lr: 0.000250. clip: 0.100000
Iteration 4: Policy loss: -0.166682. Value loss: 0.051994. Entropy: 1.374561.
Iteration 5: Policy loss: -0.153367. Value loss: 0.041330. Entropy: 1.375694.
Iteration 6: Policy loss: -0.167738. Value loss: 0.047337. Entropy: 1.376785.
Training network. lr: 0.000250. clip: 0.100000
Iteration 7: Policy loss: -0.256462. Value loss: 0.727763. Entropy: 1.370962.
Iteration 8: Policy loss: -0.249125. Value loss: 0.479165. Entropy: 1.374830.
Iteration 9: Policy loss: -0.237247. Value loss: 0.508010. Entropy: 1.382150.
Training network. lr: 0.000250. clip: 0.100000
Iteration 10: Policy loss: -0.563716. Value loss: 2.374101. Entropy: 1.376569.
Iteration 11: Policy loss: -0.543814. Value loss: 2.030069. Entropy: 1.379307.

/usr/local/lib/python3.5/dist-packages/numpy/core/fromnumeric.py:2920: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/usr/local/lib/python3.5/dist-packages/numpy/core/_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


...

episode: 6896   score: 430.0  epsilon: 1.0    steps: 521  evaluation reward: 435.4
Training network. lr: 0.000102. clip: 0.040713
Iteration 19327: Policy loss: -0.019440. Value loss: 0.030781. Entropy: 2.685478.
Iteration 19328: Policy loss: -0.014510. Value loss: 0.016216. Entropy: 2.691503.
Iteration 19329: Policy loss: -0.017442. Value loss: 0.014495. Entropy: 2.695205.
episode: 6897   score: 440.0  epsilon: 1.0    steps: 183  evaluation reward: 436.2
Training network. lr: 0.000102. clip: 0.040713
Iteration 19330: Policy loss: 0.048598. Value loss: 0.020418. Entropy: 2.686926.
Iteration 19331: Policy loss: 0.050360. Value loss: 0.015786. Entropy: 2.691554.
Iteration 19332: Policy loss: 0.046825. Value loss: 0.015463. Entropy: 2.691249.
Training network. lr: 0.000102. clip: 0.040713
Iteration 19333: Policy loss: 0.094649. Value loss: 0.025464. Entropy: 2.718697.
Iteration 19334: Policy loss: 0.095530. Value loss: 0.016293. Entropy: 2.711522.
Iteration 19335: Policy loss: 0.094182. Va

Iteration 19394: Policy loss: 0.061223. Value loss: 0.014292. Entropy: 2.735574.
Iteration 19395: Policy loss: 0.057869. Value loss: 0.012286. Entropy: 2.734450.
episode: 6916   score: 350.0  epsilon: 1.0    steps: 396  evaluation reward: 443.6
episode: 6917   score: 410.0  epsilon: 1.0    steps: 570  evaluation reward: 444.6
episode: 6918   score: 360.0  epsilon: 1.0    steps: 732  evaluation reward: 443.9
Training network. lr: 0.000101. clip: 0.040566
Iteration 19396: Policy loss: 0.059578. Value loss: 0.031412. Entropy: 2.727205.
Iteration 19397: Policy loss: 0.056633. Value loss: 0.022588. Entropy: 2.718465.
Iteration 19398: Policy loss: 0.054509. Value loss: 0.020929. Entropy: 2.718506.
Training network. lr: 0.000101. clip: 0.040566
Iteration 19399: Policy loss: 0.058412. Value loss: 0.024807. Entropy: 2.721362.
Iteration 19400: Policy loss: 0.054702. Value loss: 0.019953. Entropy: 2.719489.
Iteration 19401: Policy loss: 0.055640. Value loss: 0.013996. Entropy: 2.723854.
episode: 

Iteration 19459: Policy loss: 0.063293. Value loss: 0.025202. Entropy: 2.687689.
Iteration 19460: Policy loss: 0.072857. Value loss: 0.015096. Entropy: 2.686357.
Iteration 19461: Policy loss: 0.063048. Value loss: 0.011093. Entropy: 2.682626.
Training network. lr: 0.000101. clip: 0.040253
Iteration 19462: Policy loss: 0.049451. Value loss: 0.019614. Entropy: 2.688149.
Iteration 19463: Policy loss: 0.048528. Value loss: 0.014518. Entropy: 2.681479.
Iteration 19464: Policy loss: 0.042184. Value loss: 0.010683. Entropy: 2.687719.
episode: 6939   score: 380.0  epsilon: 1.0    steps: 144  evaluation reward: 455.2
Training network. lr: 0.000101. clip: 0.040253
Iteration 19465: Policy loss: -0.098694. Value loss: 0.461701. Entropy: 2.699854.
Iteration 19466: Policy loss: -0.099654. Value loss: 0.533758. Entropy: 2.684736.
Iteration 19467: Policy loss: -0.077814. Value loss: 0.345243. Entropy: 2.668101.
episode: 6940   score: 940.0  epsilon: 1.0    steps: 723  evaluation reward: 460.8
Training

Iteration 19526: Policy loss: -0.000376. Value loss: 0.008634. Entropy: 2.747331.
Iteration 19527: Policy loss: 0.000210. Value loss: 0.007605. Entropy: 2.747658.
episode: 6960   score: 410.0  epsilon: 1.0    steps: 925  evaluation reward: 447.2
Training network. lr: 0.000100. clip: 0.040105
Iteration 19528: Policy loss: 0.017743. Value loss: 0.019385. Entropy: 2.771859.
Iteration 19529: Policy loss: 0.019828. Value loss: 0.011228. Entropy: 2.768120.
Iteration 19530: Policy loss: 0.019084. Value loss: 0.008857. Entropy: 2.767966.
episode: 6961   score: 430.0  epsilon: 1.0    steps: 455  evaluation reward: 448.6
Training network. lr: 0.000100. clip: 0.040105
Iteration 19531: Policy loss: 0.028981. Value loss: 0.012139. Entropy: 2.786672.
Iteration 19532: Policy loss: 0.027138. Value loss: 0.009603. Entropy: 2.789460.
Iteration 19533: Policy loss: 0.025878. Value loss: 0.008371. Entropy: 2.787711.
episode: 6962   score: 240.0  epsilon: 1.0    steps: 201  evaluation reward: 446.2
episode:

Iteration 19592: Policy loss: 0.058940. Value loss: 0.011879. Entropy: 2.797616.
Iteration 19593: Policy loss: 0.056339. Value loss: 0.009675. Entropy: 2.799191.
episode: 6982   score: 450.0  epsilon: 1.0    steps: 917  evaluation reward: 418.2
Training network. lr: 0.000100. clip: 0.039949
Iteration 19594: Policy loss: -0.038987. Value loss: 0.019247. Entropy: 2.765777.
Iteration 19595: Policy loss: -0.042894. Value loss: 0.012690. Entropy: 2.766421.
Iteration 19596: Policy loss: -0.035663. Value loss: 0.011156. Entropy: 2.766535.
episode: 6983   score: 330.0  epsilon: 1.0    steps: 29  evaluation reward: 412.3
Training network. lr: 0.000100. clip: 0.039949
Iteration 19597: Policy loss: -0.001225. Value loss: 0.014714. Entropy: 2.790957.
Iteration 19598: Policy loss: -0.004411. Value loss: 0.011715. Entropy: 2.790993.
Iteration 19599: Policy loss: -0.003121. Value loss: 0.011040. Entropy: 2.790483.
episode: 6984   score: 420.0  epsilon: 1.0    steps: 874  evaluation reward: 413.1
Trai